In [81]:
%reset -f
%load_ext autoreload
%autoreload 2

import os
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib as mpl
from IPython.display import HTML
from pybounds import Simulator

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [82]:
from double_pendulum import DoublePendulumParameters, DoublePendulumModel, DoublePendulumDrawer

# Set model parameters

In [83]:
dt = 0.05  #  time-step [s]

In [84]:
params = DoublePendulumParameters(
    g= 0,  # gravity
    k_1=0.0, k_2=1.0,  # torsional stiffness
    c_1=1.0, c_2=1.0,  # torsional damping
    L_1=1.0, L_2=1.0,  # length
    m_1=1.0, m_2=1.0,  # mass
    c_w_1=2.0, c_w_2=2.0,  # wind damping
    J_1=None, J_2=None,  # inertia automatically computed based on cylinder model
)
model = DoublePendulumModel(parameters=params)
model.parameters.__dict__

{'g': 0,
 'L_1': 1.0,
 'L_2': 1.0,
 'k_1': 0.0,
 'k_2': 1.0,
 'c_1': 1.0,
 'c_2': 1.0,
 'm_1': 1.0,
 'm_2': 1.0,
 'c_w_1': 2.0,
 'c_w_2': 2.0,
 'J_1': 0.08333333333333333,
 'J_2': 0.08333333333333333}

# Construct simulator object

In [85]:
simulator = Simulator(model.f, model.h,
                      dt=dt,
                      state_names=model.state_names,
                      input_names=model.input_names,
                      measurement_names=model.measurement_names)

# Set initial condition & inputs

In [86]:
T = 10.0  # total time [s]
tsim = np.arange(start=0.0, stop=T + 1e-3, step=dt)  # time vector [s]

In [87]:
# Initial conditions
x0 = {'theta_1': 0,
      'theta_2': np.pi/4,
      'theta_dot_1': 0.0,
      'theta_dot_2': 0.0,
      'x': 0.0,
      'y': 0.0,
      'x_dot': 0.0,
      'y_dot': 0.0,
      }

In [88]:
# Inputs
u = {'x_ddot': -0.05 + 0.2*np.cos(2*np.pi*(1/T) * tsim),  # x-acceleration of base
     'y_ddot': -0.05 + 0.2*np.sin(2*np.pi*(1/T) * tsim),  # y-acceleration of base
     'tau_1': 0.0*np.ones_like(tsim),  # torque on 1st segment
     'tau_2': 0.0*np.ones_like(tsim), # torque on 2nd segment
     }

# Run simulation in open-loop

In [89]:
t_sim, x_sim, u_sim, y_sim = simulator.simulate(x0=x0, mpc=False, u=u, return_full_output=True)
sim_data = pd.DataFrame(y_sim)
sim_data.insert(0, 'time', t_sim)
sim_data

time   theta_1   theta_2  theta_dot_1  theta_dot_2         x         y  \
0     0.00  0.000000  0.785398     0.000000     0.000000  0.000000  0.000000   
1     0.05  0.002386  0.780840     0.089511    -0.169131  0.000188 -0.000063   
2     0.10  0.008466  0.769570     0.149724    -0.272938  0.000750 -0.000242   
3     0.15  0.017028  0.754278     0.190067    -0.332785  0.001687 -0.000523   
4     0.20  0.027240  0.736797     0.216461    -0.362402  0.002997 -0.000890   
..     ...       ...       ...          ...          ...       ...       ...   
196   9.80  0.848407  0.915089    -0.123369    -0.125396 -2.347009  0.781602   
197   9.85  0.842350  0.908903    -0.118938    -0.122032 -2.373316  0.757165   
198   9.90  0.836515  0.902886    -0.114503    -0.118647 -2.399251  0.732548   
199   9.95  0.830902  0.897038    -0.110066    -0.115242 -2.424813  0.707767   
200  10.00  0.825511  0.891362    -0.105628    -0.111819 -2.450000  0.682837   

        x_dot     y_dot    w  zeta    x_ddot    y_ddot  tau_1  tau_2  \
0    0.000000  0.000000  1.0   1.0  0.150000 -0.050000    0.0    0.0   
1    0.007500 -0.002500  1.0   1.0  0.149901 -0.043718    0.0    0.0   
2    0.014995 -0.004686  1.0   1.0  0.149605 -0.037442    0.0    0.0   
3    0.022475 -0.006558  1.0   1.0  0.149112 -0.031178    0.0    0.0   
4    0.029931 -0.008117  1.0   1.0  0.148423 -0.024933    0.0    0.0   
..        ...       ...  ...   ...       ...       ...    ...    ...   
196 -0.529852 -0.486864  1.0   1.0  0.148423 -0.075067    0.0    0.0   
197 -0.522431 -0.490617  1.0   1.0  0.149112 -0.068822    0.0    0.0   
198 -0.514975 -0.494058  1.0   1.0  0.149605 -0.062558    0.0    0.0   
199 -0.507495 -0.497186  1.0   1.0  0.149901 -0.056282    0.0    0.0   
200 -0.500000 -0.500000  1.0   1.0  0.150000 -0.050000    0.0    0.0   

     theta_2_1  
0     0.785398  
1     0.778453  
2     0.761104  
3     0.737250  
4     0.709557  
..         ...  
196   0.066682  
197   0.066553  
198   0.066371  
199   0.066136  
200   0.065851  

[201 rows x 16 columns]

# Animate

In [90]:
plt.rcParams['animation.embed_limit'] = 100

In [91]:
drawer = DoublePendulumDrawer(
    sim_data['x'].values,
    sim_data['y'].values,
    sim_data['theta_1'].values,
    sim_data['theta_2'].values,
    L1=model.parameters.L_1,
    L2=model.parameters.L_2,
    seg1_kwargs=dict(color='blue', linewidth=4.0, markersize=7),
    seg2_kwargs=dict(color='red', linewidth=4.0, markersize=7),
    trail1=True, trail2=True, trail_base=True
)

In [92]:
# Make figure
fig, ax = plt.subplots(nrows=1, ncols=1)

def update(frame):
    ax.clear()
    drawer.draw(ax, frame=frame)
    ax.set_aspect('equal')
    ax.axis(drawer.get_axis_bounds())

# Make animation
animation = mpl.animation.FuncAnimation(
    fig, update,
    frames=sim_data.shape[0],
    blit=False,
    interval=int(1000 * dt))

# update(0)
plt.close(fig)

In [93]:
# Display it
HTML(animation.to_jshtml())

In [94]:
# Save it
# from matplotlib.animation import PillowWriter
# save_path = os.path.join(os.path.pardir, 'animation', 'example_open_loop.gif')
# animation.save(save_path, PillowWriter(fps=int(1/dt)))